#Mapas Finales

En este caso se desarrollan mapas de Covid-19 en Costa Rica y Guatemala, en conjunto con datos de movilidad en ambos países. Además, se genera un mapa de riesgo ante el Covid-19 en Guatemala. 

In [1]:
%%capture
!pip install geopandas
!pip install -U kaleido

In [ ]:
data_mov = pd.read_csv('Mov_CR.txt', decimal = '.', sep='\t')
data_mov

departamento  San José  Alajuela  Cartago  Heredia  Guanacaste  Puntarenas  \
0     San José   0.85885   0.08293  0.22093  0.23998     0.01082     0.01931   
1     Alajuela   0.01922   0.81398  0.00917  0.05058     0.00818     0.01167   
2      Cartago   0.01452   0.00145  0.69690  0.00432     0.00192     0.00079   
3      Heredia   0.05240   0.06027  0.01997  0.65428     0.00302     0.00369   
4   Guanacaste   0.00181   0.00483  0.00136  0.00186     0.94854     0.00647   
5   Puntarenas   0.00655   0.00923  0.00248  0.00239     0.01239     0.94241   
6        Limón   0.00278   0.00247  0.01043  0.00523     0.00217     0.00348   

     Limón  
0  0.02058  
1  0.00179  
2  0.00225  
3  0.00656  
4  0.00080  
5  0.00066  
6  0.95579

In [12]:
import geopandas as gpd
import plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import sys
import numpy as np
import os

    #Esta función permite graficar los datos de casos acumulados de Covid-19 y de movilidad para cada departamento 

def Cov_Mov_map(departamento, fecha):

#Se leen los datos
  data_mov = pd.read_csv('Mov_CR.txt', decimal = '.', sep='\t')
  data_acums = pd.read_csv('Acums_Cov.txt', decimal = ',', sep='\t')
  df_admin = gpd.read_file('/content/provincias.json')
  centroides = pd.read_csv('centroides_provin_CR.txt',sep ='\t')
  centroides['X'] = centroides['X']*-1
  os.makedirs('Vis_Esp_Covid19',exist_ok=True)

#Se filtran los datos de movilidad por condiciones y valores y se asignan a name como un str
  condiciones = [
      (data_mov[departamento] >= 0.0007) & (data_mov[departamento] <0.002),
      (data_mov[departamento] >= 0.002) & (data_mov[departamento] <0.003),
      (data_mov[departamento] >= 0.003) & (data_mov[departamento] <0.05),
      (data_mov[departamento] >= 0.05) & (data_mov[departamento] <0.96)
      ]

  valores = ['[0.0007 - 0.002)', '[0.002 - 0.003)', '[0.003 - 0.05)','[0.05 - 0.96)']

#Se filtran los datos de movilidad
  data_mov['rango'] = np.select(condiciones, valores)
  data_mov = data_mov.sort_values('rango')

#Se aplica una escala logarítmica a los datos de Covid-19 acumulados
  data_acums['log_scale'] = np.log10(data_acums[fecha])
  Estado = 'log_scale' 
  Place = 'provincia'
  Escala = 'Blues'

    #Se crea la figura de mapa con choropleth
    #Recibe el archivo csv con los datos, y el json con el mapa
    #locations se utiliza para escoger la columna que se quiere leer con el nombre del lugar
    #color escoge la columna que tiene los datos que se quieren representar y realiza la barra de colores


  fig = px.choropleth(data_frame=data_acums, 
                              geojson=df_admin, 
                              locations=Place, 
                              hover_name=Place,
                              featureidkey='properties.name',
                              color = Estado, 
                              color_continuous_scale=Escala,
                              labels={ Estado: 'No. Cases'},
                             )

    #Se mueve la barra de colores
  fig.update_layout(coloraxis_colorbar_x=0.79, 
                    font=dict(size=20,
                    color="black")
                    )
    #Se aumenta la resolución
  fig.update_geos(resolution=110)

    #Se ajusta el margen de la imagen
  fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

    #Se quita la escala logarítmica en la barra de colores y se modifica el tamaño
  fig.update_layout(coloraxis_colorbar=dict(len=0.75, title='No. Cases',  tickvals = [0, 0.5, 1, 1.5, 2], ticktext = ['0', '5', '10', '15', '100']))    
#fig.update_layout(coloraxis_colorbar=dict(len=0.75, title='No. Cases',  tickvals = [2, 2.5, 3, 3.5, 4, 4.5], ticktext = ['0', '500', '1k', '2k', '16k']))

     #se generan las líneas correspondientes para cada derpartamento en la capa de movilidad
  for i in range(0,len(centroides['departamento'])):

    fig.add_trace(
          go.Scattergeo(
              lon = [centroides['X'][data_mov.columns.get_loc(departamento)-1], centroides['X'][i]],
              lat = [centroides['Y'][data_mov.columns.get_loc(departamento)-1], centroides['Y'][i]],
              mode = 'lines',
              line = dict(width = data_mov[departamento][i]*1,color = 'orange'),
              opacity = 0.9,
              showlegend=False
            )
        )



  ints = []
  for i in data_mov['rango']:
      if i not in ints:
          ints.append(i)
  ints.sort()


     #Se generan los marcadores de movilidad de acuerdo al índice empleado

  for i in range(0,len(centroides['departamento'])):
    fig.add_trace(
          go.Scattergeo(
              lon = [centroides['X'][i]],
              lat = [centroides['Y'][i]],
              name=str(data_mov['rango'][i]), 
              mode = 'markers',
              marker = dict(size = data_mov[departamento][i]*50, color = 'orange'),
              opacity = 0.9,  
              legendgroup =  data_mov['rango'][i],
              showlegend=False      
            )
        )


    #Se crean las leyendas de los marcadores
  fig.add_trace(
         go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=35, color='orange'),
                         legendgroup='[0.05 - 0.96)', showlegend=True, name='[0.05 - 0.96)'))

  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=10, color='orange'),
                         legendgroup='[0.003 - 0.005)', showlegend=True, name='[0.003 - 0.05)'))

  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=6, color='orange'),
                         legendgroup='[0.002 - 0.003)', showlegend=True, name='[0.002 - 0.003)'))
  
  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=2, color='orange'),
                         legendgroup='[0.0007 - 0.002)', showlegend=True, name='[0.0007 - 0.002)'))

          

  #Se da formato a las leyendas de los marcadores

  fig.update_layout(legend_title_text='Mobility from '+departamento,
      legend=dict(
          x=0.005,
          y=0.83,
          title_font_family="Arial",
          font=dict(
              #family="Courier",
              size=14,
              color="black"
          ),
          bgcolor="LightBlue",
          bordercolor="Black",
          borderwidth=1
      )
  )



     #Se ajusta el tamaño de la barra de color
  fig.update_layout(coloraxis_colorbar=dict(yanchor="middle"))   

    #Formato visual para la figura

  dates = pd.to_datetime(data_acums.columns[1])
  año = dates.year
  mes = dates.month
  dia = dates.day


    #Título de la imagen
#fig.update_layout(
 #       title_text = 'Covid-19 cumulative cases in Guatemala'+': '+str(dia)+'-'+str(mes)+'-'+str(año),
  #      font=dict(
   #         size=18,
    #        color="#7f7f7f"
     #   )
   # )


    #Se eliminan los otros paises y limites que vienen por defecto en el choropleth para que sólo aparezca Guatemala
  fig.update_geos(showcountries=False, showcoastlines=False, showland=False, showframe = False, framewidth = 10, fitbounds="locations")
  fig.write_image("""Vis_Esp_Covid19/"""+str(dia)+'-'+str(mes)+'-'+str(año)+'_CR'+""".pdf""")
  return fig


  #fig.show()

    #Se exporta la imagen como pdf
  


Cov_Mov_map('Cartago','1/5/2020')

In [13]:

import geopandas as gpd
import plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import sys
import numpy as np
import os


    #Esta función permite graficar los datos de casos acumulados de Covid-19 y de movilidad para cada departamento o provincia
def Cov_Mov_map(departamento, fecha):

#Se leen los datos
  xls = pd.ExcelFile('MovilidadGuatemala.xlsx')
  xls.sheet_names
  data_mov = xls.parse(sheet_name='Hoja1')
  data_acums = pd.read_csv('Acums_días.txt', decimal = ',', sep='\t')
  df_admin = gpd.read_file('/content/stanford-vx042ws8701-geojson.json')
  centroides = pd.read_csv('centroides_depar_Guatemala.txt',sep ='\t')
  centroides['X'] = centroides['X']*-1
  os.makedirs('Vis_Esp_Covid19',exist_ok=True)

#Se filtran los datos de movilidad por condiciones y valores y se asignan a name como un str
  condiciones = [
      (data_mov[departamento] >= 0) & (data_mov[departamento] <0.0005),
      (data_mov[departamento] >= 0.0005) & (data_mov[departamento] <0.0007),
      (data_mov[departamento] >= 0.0007) & (data_mov[departamento] <0.002),
      (data_mov[departamento] >= 0.002) & (data_mov[departamento] <0.003),
      (data_mov[departamento] >= 0.003) & (data_mov[departamento] <0.005)
      ]

  valores = ['[0 - 0.0005)', '[0.0005 - 0.0007)', '[0.0007 - 0.002)', '[0.002 - 0.003)', '[0.003 - 0.02)']

#Se filtran los datos de movilidad
  data_mov['rango'] = np.select(condiciones, valores)
  data_mov = data_mov.sort_values('rango')

#Se aplica una escala logarítmica a los datos de Covid-19 acumulados
  data_acums['log_scale'] = np.log10(data_acums[fecha])
  Estado = 'log_scale' 
  Place = 'departamento'
  Escala = 'Blues'

    #Se crea la figura de mapa con choropleth
    #Recibe el archivo csv con los datos, y el json con el mapa
    #locations se utiliza para escoger la columna que se quiere leer con el nombre del lugar
    #color escoge la columna que tiene los datos que se quieren representar y realiza la barra de colores


  fig = px.choropleth(data_frame=data_acums, 
                              geojson=df_admin, 
                              locations=Place, 
                              hover_name=Place,
                              featureidkey='properties.name_1',
                              color = Estado, 
                              color_continuous_scale=Escala,
                              labels={ Estado: 'No. Cases'},
                             )

    #Se mueve la barra de colores
  fig.update_layout(coloraxis_colorbar_x=0.79, 
                    font=dict(size=20,
                    color="black")
                    )
    #Se aumenta la resolución
  fig.update_geos(resolution=110)

    #Se ajusta el margen de la imagen
  fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

    #Se quita la escala logarítmica en la barra de colores y se modifica el tamaño
  fig.update_layout(coloraxis_colorbar=dict(len=0.75, title='No. Cases',  tickvals = [0, 0.5, 1, 1.5, 2], ticktext = ['0', '5', '10', '15', '100']))    
#fig.update_layout(coloraxis_colorbar=dict(len=0.75, title='No. Cases',  tickvals = [2, 2.5, 3, 3.5, 4, 4.5], ticktext = ['0', '500', '1k', '2k', '16k']))

     #se generan las líneas correspondientes para cada derpartamento en la capa de movilidad
  for i in range(0,len(centroides['departamento'])):

    fig.add_trace(
          go.Scattergeo(
              lon = [centroides['X'][data_mov.columns.get_loc(departamento)-1], centroides['X'][i]],
              lat = [centroides['Y'][data_mov.columns.get_loc(departamento)-1], centroides['Y'][i]],
              mode = 'lines',
              line = dict(width = data_mov[departamento][i]*1000,color = 'orange'),
              opacity = 0.9,
              showlegend=False
            )
        )



  ints = []
  for i in data_mov['rango']:
      if i not in ints:
          ints.append(i)
  ints.sort()


     #Se generan los marcadores de movilidad de acuerdo al índice empleado

  for i in range(0,len(centroides['departamento'])):
    fig.add_trace(
          go.Scattergeo(
              lon = [centroides['X'][i]],
              lat = [centroides['Y'][i]],
              name=str(data_mov['rango'][i]), 
              mode = 'markers',
              marker = dict(size = data_mov[departamento][i]*5000, color = 'orange'),
              opacity = 0.9,  
              legendgroup =  data_mov['rango'][i],
              showlegend=False      
            )
        )


    #Se crean las leyendas de los marcadores
  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=20, color='orange'),
                         legendgroup='[0.003 - 0.005)', showlegend=True, name='[0.003 - 0.02)'))

  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=9, color='orange'),
                         legendgroup='[0.002 - 0.003)', showlegend=True, name='[0.002 - 0.003)'))

  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=4, color='orange'),
                         legendgroup='[0.0007 - 0.002)', showlegend=True, name='[0.0007 - 0.002)'))

  fig.add_trace(
          go.Scattergeo(lon=[None], lat=[None], mode='markers',
                         marker=dict(size=1, color='orange'),
                         legendgroup='[0.0001 - 0.0005)', showlegend=True, name='[0.0001 - 0.0005)'))

          

  #Se da formato a las leyendas de los marcadores

  fig.update_layout(legend_title_text='Mobility from '+departamento,
      legend=dict(
          x=0.005,
          y=0.83,
          title_font_family="Arial",
          font=dict(
              #family="Courier",
              size=14,
              color="black"
          ),
          bgcolor="LightBlue",
          bordercolor="Black",
          borderwidth=1
      )
  )



     #Se ajusta el tamaño de la barra de color
  fig.update_layout(coloraxis_colorbar=dict(yanchor="middle"))   

    #Formato visual para la figura

  dates = pd.to_datetime(data_acums.columns[1])
  año = dates.year
  mes = dates.month
  dia = dates.day


    #Título de la imagen
#fig.update_layout(
 #       title_text = 'Covid-19 cumulative cases in Guatemala'+': '+str(dia)+'-'+str(mes)+'-'+str(año),
  #      font=dict(
   #         size=18,
    #        color="#7f7f7f"
     #   )
   # )


    #Se eliminan los otros paises y limites que vienen por defecto en el choropleth para que sólo aparezca Guatemala
  fig.update_geos(showcountries=False, showcoastlines=False, showland=False, showframe = False, framewidth = 10, fitbounds="locations")
  fig.write_image("""Vis_Esp_Covid19/"""+str(dia)+'-'+str(mes)+'-'+str(año)+'_GT'+""".pdf""")
  return fig


  #fig.show()

    #Se exporta la imagen como pdf
  


Cov_Mov_map('Guatemala','5/1/2020')

In [ ]:
    #Se importan las librerías
import geopandas as gpd
import plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import sys
import numpy as np
import os

    #Se leen los datos  
df_admin = gpd.read_file('/content/stanford-vx042ws8701-geojson.json')
xls = pd.ExcelFile('MapaRiesgo.xlsx')
xls.sheet_names
data_riesgo = xls.parse(sheet_name='IndicadoresGT.csv')

data_riesgo['Riesgo'] = data_riesgo['Riesgo'].astype(str) 

    #Se genera el mapa con datos de riesgo
fig = px.choropleth(data_riesgo, 
                    geojson=df_admin,
                    locations= 'Depto',
                    color = 'Riesgo',
                    range_color=(5,1),
                    hover_name = 'Depto',                    
                    featureidkey='properties.name_1',
                    labels={ 'Riesgo': 'Risk'},
                    color_discrete_map={'1': "#08306b",         
                                        '2':'#2171b5',
                                        '3':'#57a0ce',
                                        '4':'#b3d2e9',
                                        '5':'#deebf7'})
    #Se da formato a la imagen
fig.update_layout(legend_x=0.68, 
                  font=dict(size=16,
                  color="black")
                  )
fig.update_layout(legend_y=0.85, 
                  font=dict(size=16,
                  color="black")
                  )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

     #Se ajusta el tamaño de la barra de color
fig.update_layout(coloraxis_colorbar=dict(yanchor="middle"))     

    #Se eliminan los otros paises y limites que vienen por defecto en el choropleth para que sólo aparezca Guatemala
fig.update_geos(showcountries=False, showcoastlines=False, showland=False, showframe=False, fitbounds="locations")


fig.show()
#fig.write_image("""Vis_Esp_Covid19/"""+str(año)+'-'+str(mes)+'-'+str(dia)+""".pdf""")

/usr/local/lib/python3.7/dist-packages/openpyxl/worksheet/_reader.py:312: UserWarning:

Unknown extension is not supported and will be removed

